In [4]:
# move stock with x years data or more to folder
# check stock data csv's for average time covered
# if the stock has 11 or more years of data, then it is a good candidate
# move those with 11+ years to a new folder

import os
import shutil 
import pandas as pd
from concurrent.futures import ProcessPoolExecutor
from functools import partial

def make_tz_naive(df):
    if df.index.tzinfo is not None:
        df.index = df.index.tz_localize(None)
    return df

def process_single_file(filename, directory):
    filepath = os.path.join(directory, filename)
    ticker = filename.replace('.csv', '')
    
    try:
        # Check if file is empty
        if os.path.getsize(filepath) == 0:
            return ticker, {'error': 'empty_file'}
            
        # Read CSV file
        df = pd.read_csv(filepath)
        
        if df.empty:
            return ticker, {'error': 'empty_dataframe'}
            
        if 'date' not in df.columns:
            return ticker, {'error': 'no_date_column'}
        
        # Process dates
        df.set_index('date', inplace=True)
        try:
            df.index = pd.to_datetime(df.index, format='ISO8601', utc=True)
        except ValueError:
            try:
                df.index = pd.to_datetime(df.index, format='%Y-%m-%d %H:%M:%S')
            except ValueError:
                df.index = pd.to_datetime(df.index, format='%Y-%m-%d')
        
        df = make_tz_naive(df)
        
        # Calculate metrics
        full_date_range = pd.date_range(start=df.index.min(), end=df.index.max(), freq='D')
        missing_dates = full_date_range.difference(df.index)
        start_date = df.index.min()
        end_date = df.index.max()
        days_covered = (end_date - start_date).days
        
        return ticker, {
            'start_date': start_date.strftime('%Y-%m-%d %H:%M:%S'),
            'end_date': end_date.strftime('%Y-%m-%d %H:%M:%S'),
            'days_covered': days_covered,
            'num_records': len(df),
            'missing_dates': len(missing_dates),
            'first_missing': missing_dates[:5].tolist() if len(missing_dates) > 0 else []
        }
        
    except Exception as e:
        return ticker, {'error': str(e)}

def analyze_market_data_coverage(years_threshold):
    # Get absolute paths
    directory = os.path.join(os.getcwd(), 'stock_data', 'all')  # Changed source directory
    target_dir = os.path.join(os.getcwd(), 'stock_data', f'{years_threshold}+yrs')  # Changed target directory
    
    if not os.path.exists(directory):
        print(f"\nError: Directory '{directory}' does not exist")
        return
    
    # Create target directory if it doesn't exist
    if not os.path.exists(target_dir):
        os.makedirs(target_dir)
        print(f"\nCreated directory: {target_dir}")
    
    # Get list of CSV files (modified filter)
    files = []
    for f in os.listdir(directory):
        file_path = os.path.join(directory, f)
        if f.endswith('.csv') and os.path.isfile(file_path):
            files.append(f)
    total_files = len(files)
    
    # Process files in parallel
    with ProcessPoolExecutor() as executor:
        process_func = partial(process_single_file, directory=directory)
        results = list(executor.map(process_func, files))
    
    # Separate results and count each category
    coverage_data = {}
    errors = []
    empty_files = []
    
    for ticker, result in results:
        if 'error' in result:
            if result['error'] in ['empty_file', 'empty_dataframe']:
                empty_files.append(f"{ticker}.csv")
            else:
                errors.append(f"Error processing {ticker}.csv: {result['error']}")
        else:
            coverage_data[ticker] = result
    
    # Print coverage statistics
    print(f"\nFile Processing Summary:")
    print(f"Total CSV files: {total_files}")
    print(f"Successfully processed: {len(coverage_data)}")
    print(f"Empty files: {len(empty_files)}")
    print(f"Errors: {len(errors)}")
    print(f"Total processed: {len(coverage_data) + len(empty_files) + len(errors)}")
    
    # Verify all files were accounted for
    total_processed = len(coverage_data) + len(empty_files) + len(errors)
    if total_processed != total_files:
        print(f"\nWARNING: Not all files were processed!")
        print(f"Missing: {total_files - total_processed} files")

    # Print results (same as before)
    if empty_files:
        print("\nEmpty files found:")
        for file in empty_files:
            print(f"- {file}")            
    print(f"\nAnalyzed {len(coverage_data)} files successfully")
    
    if coverage_data:
        total_days = sum(data['days_covered'] for data in coverage_data.values())
        avg_days = total_days / len(coverage_data)
        print(f"Average coverage: {avg_days:.2f} days ({avg_days/365:.2f} years)")
        print("\nDetailed coverage by ticker:")
        
        for ticker, data in coverage_data.items():
            print(f"\n{ticker}:")
            print(f"  Start: {data['start_date']}")
            print(f"  End: {data['end_date']}")
            print(f"  Days covered: {data['days_covered']}")
            print(f"  Records: {data['num_records']}")
            print(f"  Missing dates: {data['missing_dates']}")
            if data['first_missing']:
                print("  First few missing dates:")
                for date in data['first_missing']:
                    print(f"    - {date}")
    
    if errors:
        print("\nErrors encountered:")
        for error in errors:
            print(f"- {error}")
    
    copied_files = []  # Changed from moved_files
    for ticker, data in coverage_data.items():
        years_covered = data['days_covered'] / 365
        if years_covered >= years_threshold:
            source_file = os.path.join(directory, f"{ticker}.csv")
            target_file = os.path.join(target_dir, f"{ticker}.csv")
            
            # Skip if target file already exists
            if os.path.exists(target_file):
                print(f"Skipping {ticker}.csv - already exists in target directory")
                continue
                
            try:
                # Copy the file
                shutil.copy2(source_file, target_file)
                copied_files.append(ticker)
            except Exception as e:
                print(f"\nError copying {ticker}.csv: {str(e)}")

    # Update the summary messages
    print(f"\nCopied {len(copied_files)} files with {years_threshold}+ years of data to {target_dir}")
    if copied_files:
        print("Copied tickers:")
        for ticker in copied_files:
            print(f"- {ticker}")

    return coverage_data

#! change this if you want to create a different threshold
years_threshold = 11
coverage_info = analyze_market_data_coverage(years_threshold)


Created directory: /home/erik/Repos/LSTM/stock_data/11+yrs

File Processing Summary:
Total CSV files: 9651
Successfully processed: 9651
Empty files: 0
Errors: 0
Total processed: 9651

Analyzed 9651 files successfully
Average coverage: 4607.55 days (12.62 years)

Detailed coverage by ticker:

_QLIB_CON:
  Start: 2024-07-25 00:00:00
  End: 2024-07-25 00:00:00
  Days covered: 0
  Records: 1
  Missing dates: 0

_QLIB_PRN:
  Start: 2006-10-12 00:00:00
  End: 2024-07-23 18:05:39
  Days covered: 6494
  Records: 4473
  Missing dates: 2023
  First few missing dates:
    - 2006-10-14 00:00:00
    - 2006-10-15 00:00:00
    - 2006-10-21 00:00:00
    - 2006-10-22 00:00:00
    - 2006-10-28 00:00:00

^DJI:
  Start: 1992-01-02 00:00:00
  End: 2024-07-23 21:14:20
  Days covered: 11891
  Records: 8199
  Missing dates: 3694
  First few missing dates:
    - 1992-01-04 00:00:00
    - 1992-01-05 00:00:00
    - 1992-01-11 00:00:00
    - 1992-01-12 00:00:00
    - 1992-01-18 00:00:00

^GSPC:
  Start: 1927-12-

In [6]:
import numpy as np
import pandas as pd
import os

def standardize_csv_format(input_path, output_path):
    # Check if file exists
    if not os.path.exists(input_path):
        print(f"Error: File {input_path} does not exist")
        return None
        
    # Get ticker from filename
    ticker = os.path.basename(input_path).replace('.csv', '')
    
    try:
        # Read the CSV file
        df = pd.read_csv(input_path)
        
        # Check if dataframe is empty
        if df.empty:
            print(f"Error: No data found in {input_path}")
            return None
            
        # Define required columns with ticker prefix
        base_columns = ['Open', 'High', 'Low', 'Close', 'Volume', 'Dividends', 'Stock Splits']
        required_columns = [f'{ticker}_{col}' for col in base_columns]
        
        # Create mapping for existing columns
        column_mapping = {}
        for existing_col in df.columns:
            # Skip 'date' column
            if existing_col.lower() == 'date':
                continue
            # Find matching base column
            for i, base_col in enumerate(base_columns):
                if base_col.lower() in existing_col.lower():
                    column_mapping[existing_col] = required_columns[i]
                    break
        
        # Create new dataframe with standardized format
        final_df = pd.DataFrame()
        
        # Handle date column
        if 'date' in df.columns:
            final_df['date'] = pd.to_datetime(df['date'], utc=True)
        else:
            final_df['date'] = pd.to_datetime(df.index, utc=True)
        
        # Add all required columns in order
        for old_col, new_col in column_mapping.items():
            final_df[new_col] = df[old_col]
            
        # Add missing columns as NaN
        for required_col in required_columns:
            if required_col not in final_df.columns:
                final_df[required_col] = np.nan
        
        # Ensure columns are in the correct order
        final_cols = ['date'] + required_columns
        final_df = final_df[final_cols]
        
        # Save the standardized CSV
        final_df.to_csv(output_path, index=False)
        return final_df
        
    except Exception as e:
        print(f"Error processing {input_path}: {str(e)}")
        return None

def process_file(file, base_dir, output_dir):
    input_path = os.path.join(base_dir, file)
    output_path = os.path.join(output_dir, file)
    print(f"Standardizing {file}...")
    return standardize_csv_format(input_path, output_path)

def process_stock_directory():
    # Updated paths
    base_dir = os.path.join(os.getcwd(), 'stock_data', '11+yrs')
    output_dir = os.path.join(os.getcwd(), 'stock_data', '11+yrs_formatted')
    
    if not os.path.exists(base_dir):
        print(f"Directory {base_dir} does not exist")
        return
        
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
        print(f"Created directory: {output_dir}")
    
    files = [f for f in os.listdir(base_dir) if f.endswith('.csv')]
    print(f"Processing {len(files)} files in 11+yrs directory")
    
    with ProcessPoolExecutor() as executor:
        process_func = partial(process_file, base_dir=base_dir, output_dir=output_dir)
        results = list(executor.map(process_func, files))
    
    print("Finished processing all files")
    print(f"Formatted files saved to: {output_dir}")
    
# Run the processing
process_stock_directory()

Created directory: /home/erik/Repos/LSTM/stock_data/11+yrs_formatted
Processing 3862 files in 11+yrs directory
Standardizing _QLIB_PRN.csv...

Standardizing ABBV.csv...Standardizing ^GSPC.csv...Standardizing ^NDX.csv...
Standardizing AACG.csv...Standardizing A.csv...Standardizing AAME.csv...Standardizing AADR.csv...Standardizing AAL.csv...Standardizing AAON.csv...Standardizing AAP.csv...Standardizing AAPL.csv...Standardizing AAT.csv...Standardizing AAXJ.csv...Standardizing AB.csv...











Standardizing ^DJI.csv...
Standardizing ABCB.csv...
Standardizing ABEO.csv...Standardizing ABEV.csv...

Standardizing ABG.csv...
Standardizing ABIO.csv...Standardizing ABM.csv...
Standardizing ABR.csv...
Standardizing ABT.csv...

Standardizing ABUS.csv...
Standardizing ABVC.csv...
Standardizing ACAD.csv...
Standardizing ACCO.csv...
Standardizing ACGL.csv...
Standardizing ACHC.csv...Standardizing ACHV.csv...

Standardizing ACIC.csv...Standardizing ACIW.csv...

Standardizing ACLS.csv...
Standardizi

/tmp/ipykernel_87246/271759729.py:44: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  final_df['date'] = pd.to_datetime(df['date'], utc=True)


Standardizing CNS.csv...
Standardizing CNSL.csv...
Standardizing CNTY.csv...
Standardizing CNX.csv...
Standardizing COCP.csv...
Standardizing CODI.csv...
Standardizing COF.csv...Standardizing COFS.csv...

Standardizing COHN.csv...
Standardizing COHR.csv...
Standardizing COKE.csv...
Standardizing COLB.csv...
Standardizing COLM.csv...
Standardizing CONN.csv...
Standardizing COO.csv...
Standardizing COOP.csv...
Standardizing COP.csv...
Standardizing COPX.csv...Standardizing COR.csv...

Standardizing CORP.csv...
Standardizing CORT.csv...
Standardizing COSM.csv...Standardizing COST.csv...
Standardizing COTY.csv...

Standardizing CP.csv...
Standardizing CPA.csv...
Standardizing CPAC.csv...
Standardizing CPAY.csv...
Standardizing CPB.csv...
Standardizing CPER.csv...
Standardizing CPHC.csv...Standardizing CPHI.csv...

Standardizing CPIX.csv...Standardizing CPK.csv...Standardizing CPLP.csv...


Standardizing CPRT.csv...
Standardizing CPRX.csv...
Standardizing CPSH.csv...Standardizing CPSS.csv..

/tmp/ipykernel_87246/271759729.py:44: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  final_df['date'] = pd.to_datetime(df['date'], utc=True)


Standardizing CRMD.csv...
Standardizing CRMT.csv...
Standardizing CRNT.csv...Standardizing CRT.csv...Standardizing CROX.csv...Standardizing CRS.csv...



Standardizing CRUS.csv...


...

Standardizing UPRO.csv...
Standardizing UPS.csv...Standardizing UPV.csv...

Standardizing UPW.csv...
Standardizing URA.csv...
Standardizing URBN.csv...Standardizing URE.csv...

Standardizing URG.csv...Standardizing URI.csv...
Standardizing URTH.csv...
Standardizing URTY.csv...

Standardizing USA.csv...Standardizing USAC.csv...

Standardizing USAP.csv...
Standardizing USAS.csv...
Standardizing USAU.csv...Standardizing USB-PA.csv...

Standardizing USB-PH.csv...
Standardizing USB.csv...Standardizing USCI.csv...

Standardizing USD.csv...
Standardizing USEG.csv...
Standardizing USIG.csv...
Standardizing USIO.csv...
Standardizing USL.csv...
Standardizing USLM.csv...
Standardizing USM.csv...Standardizing USMV.csv...

Standardizing USO.csv...
Standardizing USPH.csv...
Standardizing USRT.csv...
Standardizing UST.csv...Standardizing UTF.csv...

Standardizing UTG.csv...Standardizing UTHR.csv...
Standardizing UTI.csv...

Standardizing UTL.csv...
Standardizing UTMD.csv...
Standardizing UTSI.csv...


/tmp/ipykernel_87246/271759729.py:44: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  final_df['date'] = pd.to_datetime(df['date'], utc=True)


Standardizing WKSP.csv...Standardizing WLDN.csv...

Standardizing WLFC.csv...
Standardizing WLY.csv...Standardizing WLK.csv...

Standardizing WLYB.csv...Standardizing WMB.csv...Standardizing WMK.csv...


Standardizing WNC.csv...
Standardizing WMPN.csv...Standardizing WNEB.csv...

Standardizing WNS.csv...
Standardizing WOLF.csv...
Standardizing WOOD.csv...
Standardizing WOR.csv...
Standardizing WPC.csv...
Standardizing WPM.csv...
Standardizing WPP.csv...
Standardizing WPRT.csv...Standardizing WPS.csv...


Standardizing WRB.csv...Standardizing WRLD.csv...Standardizing WRN.csv...

Standardizing WSBC.csv...
Standardizing WSFS.csv...
Standardizing WSM.csv...Standardizing WSO-B.csv...
Standardizing WSO.csv...

Standardizing WST.csv...Standardizing WSR.csv...

Standardizing WT.csv...Standardizing WTBA.csv...

Standardizing WTFC.csv...Standardizing WTI.csv...

Standardizing WTM.csv...
Standardizing WTMF.csv...
Standardizing WTRE.csv...
Standardizing WTRG.csv...
Standardizing WTS.csv...
Standar

/tmp/ipykernel_87246/271759729.py:44: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  final_df['date'] = pd.to_datetime(df['date'], utc=True)


Standardizing XOP.csv...
Standardizing XPH.csv...Standardizing XPL.csv...Standardizing XPO.csv...

Standardizing XPP.csv...

Standardizing XRAY.csv...Standardizing XRT.csv...

Standardizing XRX.csv...
Standardizing XSD.csv...
Standardizing XSLV.csv...
Standardizing XSMO.csv...Standardizing XSVM.csv...

Standardizing XSW.csv...Standardizing XTIA.csv...
Standardizing XTL.csv...

Standardizing XTLB.csv...Standardizing XTN.csv...

Standardizing XTNT.csv...
Standardizing XXII.csv...Standardizing XYL.csv...Standardizing XWEL.csv...

Standardizing XYLD.csv...

Standardizing YANG.csv...
Standardizing YCL.csv...Standardizing YELP.csv...

Standardizing YHGJ.csv...
Standardizing YINN.csv...
Standardizing YNDX.csv...Standardizing YORW.csv...
Standardizing YPF.csv...

Standardizing YUM.csv...
Standardizing YXI.csv...
Standardizing YY.csv...Standardizing YYY.csv...

Standardizing ZBRA.csv...Standardizing ZBH.csv...

Standardizing ZD.csv...
Standardizing ZEUS.csv...
Standardizing ZION.csv...Standardi